# Fine-Tuning GPT-2 on Drugs.com Reviews for Depression

**Author**: Zakia Salod

**Affiliation**: University of KwaZulu-Natal (UKZN), Durban, South Africa

**Contact**: zakia.salod@gmail.com

**Machine Used**: Google Colab T4 GPU

**Last Updated**: 9 December 2023

**Description**:
This notebook demonstrates the process of fine-tuning the GPT-2 model using the Drugs.com reviews dataset, focusing specifically on reviews related to depression. The notebook covers the steps of loading and preprocessing the dataset, initializing and preparing the GPT-2 model for fine-tuning, and the fine-tuning process itself. Post-training, the notebook illustrates how to save and push the fine-tuned model to the Hugging Face Hub. This exercise aims to enhance GPT-2's ability to generate more relevant and insightful text related to depression drug reviews.


**License**:
This work is licensed under the [Apache 2.0 License](https://www.apache.org/licenses/LICENSE-2.0). Free for educational and research use.



## STEP 1: SETTING UP THE ENVIRONMENT

### Load Necessary Libraries

In [ ]:
# Enable automatic module reloading to reflect changes in external .py files
%load_ext autoreload
# Reload all modules before executing code, keeping modules up-to-date
%autoreload 2

### Install Required Packages

In [ ]:
!pip install git+https://github.com/huggingface/transformers

  Cloning https://github.com/huggingface/transformers to /tmp/pip-req-build-44ijr861
  Running command git clone --filter=blob:none --quiet https://github.com/huggingface/transformers /tmp/pip-req-build-44ijr861
  Resolved https://github.com/huggingface/transformers to commit df5c5c62ae253055336f5bb0828ca8e3e15ab6bd
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for transformers: filename=transformers-4.36.0.dev0-py3-none-any.whl size=8195433 sha256=79b5b0d64790d529619e06ffc24ad2f2a2692b0a7d84d20a1e0c4dae56550d23
  Stored in directory: /tmp/pip-ephem-wheel-cache-ogqdggii/wheels/c0/14/d6/6c9a5582d2ac191ec0a483be151a4495fe1eb2a6706ca49f1b
Successfully built transformers
  Attempting uninstall: transformers
    Found existing installation: transformers 4.35.2
    Uninstalling transformers-4.35.2:
      Successfully uninstalled transformers-4.35.2


In [ ]:
!pip install datasets evaluate torch wandb

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 521.2/521.2 kB 8.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.1/84.1 kB 11.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 31.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 15.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 18.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 190.6/190.6 kB 23.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 252.8/252.8 kB 28.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 9.5 MB/s eta 0:00:00


In [ ]:
!pip install accelerate -U

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 265.7/265.7 kB 5.2 MB/s eta 0:00:00


In [ ]:
!pip install transformers[torch]

### Import Necessary Libraries

In [ ]:
import numpy as np
from datasets import load_dataset
from datasets import concatenate_datasets
from transformers import GPT2Tokenizer
from transformers import GPT2LMHeadModel
import html
import re
from collections import Counter
import pandas as pd

### Initialize Weights & Biases for Tracking

In [ ]:
# Import Weights & Biases for experiment tracking
import wandb

In [ ]:
# Initialize wandb for tracking and visualizing the training
wandb.init(project="gpt2-drugscom_depression_reviews")

<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

 ··········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


## STEP 2: LOAD AND PRE-PROCESS DRUG REVIEWS DATASET

In [ ]:
dataset_name = "Zakia/drugscom_reviews"

In [ ]:
ds = load_dataset(dataset_name, split="train")

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

In [ ]:
# Filter out rows with missing drugName, condition, or review
ds = ds.filter(lambda x: all([x.get("drugName"), x.get("condition"), x.get("review")]))

Filter:   0%|          | 0/161297 [00:00<?, ? examples/s]

In [ ]:
# Filter the dataset for the condition 'Depression'
ds = ds.filter(lambda example: example["condition"] == "Depression")

Filter:   0%|          | 0/160398 [00:00<?, ? examples/s]

In [ ]:
# Get the number of records
num_records = ds.num_rows
print(f"Number of records with Depression condition: {num_records}")

Number of records with Depression condition: 9069


In [ ]:
# Function to clean review text
def clean_review(text):
    # Check if the text is a string
    if not isinstance(text, str):
      return ""  # Return an empty string if the input is not a string
    text = html.unescape(text)  # Decode HTML entities
    text = re.sub(r'"', '', text)  # Remove quotes
    text = re.sub(r'<.*?>', '', text)  # Remove HTML tags
    return text

In [ ]:
# Clean the reviews of the train set
# Apply the clean_review function in a batched manner
def clean_reviews(batch):
    # Apply clean_review to each review in the batch and return the modified batch
    return {"review": [clean_review(review) for review in batch["review"]]}

In [ ]:
ds = ds.map(clean_reviews, batched=True)

Map:   0%|          | 0/9069 [00:00<?, ? examples/s]

In [ ]:
# Get the number of records
num_records = ds.num_rows
print(f"Number of records with Depression condition: {num_records}")

Number of records with Depression condition: 9069


## STEP 3: PREPARE THE GPT-2 MODEL FOR FINE-TUNING

In [ ]:
# Initialize the tokenizer
tokenizer = GPT2Tokenizer.from_pretrained("gpt2")

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/665 [00:00<?, ?B/s]

In [ ]:
# Make sure the tokenizer recognizes the pad_token
tokenizer.pad_token = tokenizer.eos_token

In [ ]:
# Function to encode the texts
def encode(examples):
    return tokenizer(examples["review"], truncation=True, padding="max_length", max_length=512)

In [ ]:
# Apply the function to the dataset
ds = ds.map(encode, batched=True)

Map:   0%|          | 0/9069 [00:00<?, ? examples/s]

In [ ]:
# Save the dataset to a file
with open("train_dataset.txt", "w", encoding="utf-8") as f:
    for example in ds:
        f.write(tokenizer.decode(example["input_ids"]) + tokenizer.eos_token + "\n")

## STEP 4: FINE-TUNING THE MODEL

In [ ]:
# Fine-tuning command for Google Colab
# Note: run_clm.py should be present in the working directory
!python run_clm.py \
    --train_file train_dataset.txt \
    --model_name_or_path gpt2 \
    --output_dir ./gpt2-drugscom_depression_reviews \
    --do_train \
    --per_device_train_batch_size 2 \
    --num_train_epochs 5 \
    --overwrite_output_dir \
    --use_fast_tokenizer True \
    --report_to "wandb"

2023-12-09 12:33:29.982409: E tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:9342] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-12-09 12:33:29.982462: E tensorflow/compiler/xla/stream_executor/cuda/cuda_fft.cc:609] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-12-09 12:33:29.982496: E tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:1518] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2023-12-09 12:33:31.101611: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
12/09/2023 12:33:39 - WARNING - __main__ - Process rank: 0, device: cuda:0, n_gpu: 1, distributed training: False, 16-bits training: False
12/09/2023 12:33:39 - INFO - __main__ - Training/evaluation parameters TrainingArguments(
_n_gpu=1,

## STEP 5: SAVE THE FINE-TUNED GPT-2 MODEL: gpt2-drugscom_depression_reviews

In [ ]:
from huggingface_hub import notebook_login # To log to our Hugging Face account to be able to upload models to the Hub.

In [ ]:
# Login to Hugging Face within the notebook
notebook_login()
!git config --global credential.helper store

In [ ]:
model_directory = "./gpt2-drugscom_depression_reviews"

In [ ]:
# Load the fine-tuned model
model = GPT2LMHeadModel.from_pretrained(model_directory)

In [ ]:
# Save and push the model to the hub
model.push_to_hub("gpt2-drugscom_depression_reviews")
tokenizer.push_to_hub("gpt2-drugscom_depression_reviews")

model.safetensors:   0%|          | 0.00/498M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/Zakia/gpt2-drugscom_depression_reviews/commit/1b4ea22d5bb925164a9a006031dd603f292807a0', commit_message='Upload tokenizer', commit_description='', oid='1b4ea22d5bb925164a9a006031dd603f292807a0', pr_url=None, pr_revision=None, pr_num=None)